In [1]:
import numpy as np
import cv2
import json

In [2]:
def crop_bottom(image, percent):
    height, width = image.shape[:2]
    cutoff = int(height * (1 - percent))
    cropped_image = image[:cutoff, :]
    return cropped_image

def crop_top(image, percent):
    height, width = image.shape[:2]
    cutoff = int(height * percent)
    cropped_image = image[cutoff:, :]
    return cropped_image

def crop_lr(image, percent):
    height, width = image.shape[:2]
    crop_width = int(width * percent)
    cropped_image = image[:, crop_width:-crop_width]
    return cropped_image


def auto_canny(image, sigma=0.33):
    v = np.median(image)
    lower = int(max(0, (1.0 - sigma) * v))
    upper = int(min(255, (1.0 + sigma) * v))
    edged = cv2.Canny(image, lower, upper)
    return edged


In [3]:
with open("/Users/omarafifi/Downloads/Jersey Detection/Data/SoccerNet/jersey-2023/train/train_gt.json") as file:
    train_labels = json.load(file)
with open("/Users/omarafifi/Downloads/Jersey Detection/Data/SoccerNet/jersey-2023/test/test_gt.json") as file:
    test_labels = json.load(file)

FileNotFoundError: [Errno 2] No such file or directory: '/Users/omarafifi/Downloads/Jersey Detection/Data/SoccerNet/jersey-2023/train/train_gt.json'

In [ ]:
train_labels['0']

10

In [ ]:
import cv2
from paddleocr import PaddleOCR as pdl

import numpy as np


img = cv2.imread('/Users/omarafifi/Downloads/Jersey Detection/Data/SoccerNet/jersey-2023/test/images/0/0_56.jpg')

ocr = pdl(use_angle_cls=True, lang='en', show_log=True)

img = crop_bottom(img, 0.5)
img = crop_top(img, 0.1)
img = crop_lr(img, 0.1)


height, width = img.shape[:2]
scale = 3.0
img = cv2.resize(img, (round(scale * width), round(scale * height)), interpolation=cv2.INTER_CUBIC)

# Reduce noise
img = cv2.GaussianBlur(img, (5, 5), 0)





result = ocr.ocr(img, cls=True)
print(result[-1][-1][-1])
#print(img)

[2024/04/23 00:06:16] ppocr DEBUG: Namespace(help='==SUPPRESS==', use_gpu=False, use_xpu=False, use_npu=False, ir_optim=True, use_tensorrt=False, min_subgraph_size=15, precision='fp32', gpu_mem=500, gpu_id=0, image_dir=None, page_num=0, det_algorithm='DB', det_model_dir='/Users/omarafifi/.paddleocr/whl/det/en/en_PP-OCRv3_det_infer', det_limit_side_len=960, det_limit_type='max', det_box_type='quad', det_db_thresh=0.3, det_db_box_thresh=0.6, det_db_unclip_ratio=1.5, max_batch_size=10, use_dilation=False, det_db_score_mode='fast', det_east_score_thresh=0.8, det_east_cover_thresh=0.1, det_east_nms_thresh=0.2, det_sast_score_thresh=0.5, det_sast_nms_thresh=0.2, det_pse_thresh=0, det_pse_box_thresh=0.85, det_pse_min_area=16, det_pse_scale=1, scales=[8, 16, 32], alpha=1.0, beta=1.0, fourier_degree=5, rec_algorithm='SVTR_LCNet', rec_model_dir='/Users/omarafifi/.paddleocr/whl/rec/en/en_PP-OCRv4_rec_infer', rec_image_inverse=True, rec_image_shape='3, 48, 320', rec_batch_num=6, max_text_length=25

In [ ]:
cv2.imwrite('/Users/omarafifi/Downloads/Jersey Detection/Data/OCR_output/im1.png',img)

True

In [ ]:
from matplotlib import pyplot as plt
import numpy as np

plt.imshow(img)

NameError: name 'img' is not defined

In [ ]:
import matplotlib.pyplot as plt
from paddleocr import PaddleOCR
from collections import Counter
import cv2, os
import pandas as pd
import random

# Initialize PaddleOCR with the English language
ocr = PaddleOCR(use_angle_cls=True, lang='en', show_log=True)

predictions = []
folder = []
ground_truth_labels = []
folder_names = []
non_detections = []


data = pd.DataFrame()

output_path = '/Users/omarafifi/Downloads/Jersey Detection/Data/OCR_output'
for i in range(0,1211):

    good_images = []

    #track number of detections
    detections = 0

    # Path to the folder containing images
    folder_path = f'/Users/omarafifi/Downloads/Jersey Detection/Data/SoccerNet/jersey-2023/train/images/{i}'

    image_files = os.listdir(folder_path)

    jersey_numbers = []

    # Iterate over each image file in the folder
    for j, file_name in enumerate(image_files):

        # Construct the full path to the image file
        image_path = os.path.join(folder_path, file_name)

        # Read the image using OpenCV
        img = cv2.imread(image_path)

        folder_length = len(folder)

        # Crop
        img = crop_bottom(img, 0.5)
        img = crop_top(img, 0.1)
        img = crop_lr(img, 0.1)



        height, width = img.shape[:2]

        # If cropped image too small, skip this folder
        if height < 1 or width < 1:
            continue
        
        # Upscale
        scale = 3.0
        img = cv2.resize(img, (round(scale * width), round(scale * height)), interpolation=cv2.INTER_CUBIC)
        img = cv2.GaussianBlur(img, (5, 5), 0)

        # Perform OCR on the image


        result = ocr.ocr(img, cls=True)

        if result != [None]:
            result = result[-1][-1][-1]  # Extract the tuple ('13', 0.9994895458221436)

            if result[0].isdigit():  # Only count numeric results (exclude detected letters)
                if result[1] > 0.2:         # Confidence threshold

                    print(f"IN FILE {file_name}: An IMAGE WAS DETECTED WITH CONFIDENCE LEVEL {result[1]}")

                    folder_names.append(file_name)
                    detections+=1

        print(file_name)

    if detections ==0:
        print(f'!!!!! NO IMAGE DETECTED FOR FOLDER: {i}')
        #select 5 random folders and add those
        for iterator in range(30):
            num = random.randint(1, folder_length)
            folder_names.append(f"{i}_{iterator}.jpg")
        non_detections.append(i)

    print(jersey_numbers)

    # Count occurrences of each value
    counts = Counter(jersey_numbers)
    # Majority vote (most common detected value is the jersey number)
    if counts:
        most_common_value = counts.most_common(1)[0][0]
    else:
        most_common_value = -1

    print('Folder:',str(i),'Jersey:',str(most_common_value))
    predictions.append(most_common_value)
    folder.append(i)

    np.array(folder_names).tofile('/Users/omarafifi/Downloads/Jersey Detection/Data/OCR_output/paddle_train.csv', sep=',')


[2024/04/23 00:06:17] ppocr DEBUG: Namespace(help='==SUPPRESS==', use_gpu=False, use_xpu=False, use_npu=False, ir_optim=True, use_tensorrt=False, min_subgraph_size=15, precision='fp32', gpu_mem=500, gpu_id=0, image_dir=None, page_num=0, det_algorithm='DB', det_model_dir='/Users/omarafifi/.paddleocr/whl/det/en/en_PP-OCRv3_det_infer', det_limit_side_len=960, det_limit_type='max', det_box_type='quad', det_db_thresh=0.3, det_db_box_thresh=0.6, det_db_unclip_ratio=1.5, max_batch_size=10, use_dilation=False, det_db_score_mode='fast', det_east_score_thresh=0.8, det_east_cover_thresh=0.1, det_east_nms_thresh=0.2, det_sast_score_thresh=0.5, det_sast_nms_thresh=0.2, det_pse_thresh=0, det_pse_box_thresh=0.85, det_pse_min_area=16, det_pse_scale=1, scales=[8, 16, 32], alpha=1.0, beta=1.0, fourier_degree=5, rec_algorithm='SVTR_LCNet', rec_model_dir='/Users/omarafifi/.paddleocr/whl/rec/en/en_PP-OCRv4_rec_infer', rec_image_inverse=True, rec_image_shape='3, 48, 320', rec_batch_num=6, max_text_length=25

KeyboardInterrupt: 

In [ ]:
data = pd.read_csv('/Users/omarafifi/Downloads/Jersey Detection/Data/OCR_output/paddle_train.csv')
data.head()
d = np.array(data['FOLDER'][0])

In [ ]:
d

array("['0_600.jpg', '0_18.jpg', '0_576.jpg', '0_589.jpg', '0_577.jpg', '0_19.jpg', '0_8.jpg', '0_615.jpg', '0_617.jpg', '0_603.jpg', '0_602.jpg', '0_616.jpg', '0_612.jpg', '0_606.jpg', '0_607.jpg', '0_613.jpg', '0_605.jpg', '0_611.jpg', '0_21.jpg', '0_20.jpg', '0_604.jpg', '0_609.jpg', '0_580.jpg', '0_1.jpg', '0_608.jpg', '0_3.jpg', '0_12.jpg', '0_583.jpg', '0_582.jpg', '0_13.jpg', '0_2.jpg', '0_6.jpg', '0_17.jpg', '0_579.jpg', '0_586.jpg', '0_592.jpg', '0_587.jpg', '0_578.jpg', '0_16.jpg', '0_7.jpg', '0_5.jpg', '0_14.jpg', '0_591.jpg', '0_585.jpg', '0_584.jpg', '0_590.jpg', '0_15.jpg', '0_4.jpg', '1_572.jpg', '1_566.jpg', '1_558.jpg', '1_575.jpg', '1_561.jpg', '1_560.jpg', '1_574.jpg', '1_562.jpg', '1_577.jpg', '1_563.jpg', '1_13.jpg', '1_12.jpg', '1_9.jpg', '1_11.jpg', '1_29.jpg', '1_15.jpg', '1_14.jpg', '1_28.jpg', '1_16.jpg', '1_17.jpg', '1_26.jpg', '1_27.jpg', '1_33.jpg', '1_25.jpg', '1_30.jpg', '1_35.jpg', '1_23.jpg', '1_22.jpg', '1_569.jpg', '2_21.jpg', '2_20.jpg', '2_8.jpg', '

Write the predictions to a dictionary

In [ ]:
import json 

# Zip arrays A and B to create a list of tuples
key_value_pairs = zip(folder,predictions)

# Convert the list of tuples into a dictionary
json_dict = dict(key_value_pairs)

# Write the dictionary to a JSON file
with open('output.json', 'w') as json_file:
    json.dump(json_dict, json_file)

In [ ]:
def compare_json_files(file1, file2):
    with open(file1, 'r') as f1:
        data1 = json.load(f1)

    with open(file2, 'r') as f2:
        data2 = json.load(f2)

    total_pairs_b = len(data2)
    matching_pairs = 0

    for key, value in data2.items():
        if key in data1 and data1[key] == value:
            matching_pairs += 1

    if total_pairs_b > 0:
        similarity_percentage = (matching_pairs / total_pairs_b) * 100
    else:
        similarity_percentage = 0

    return similarity_percentage

# Usage
file1 = "test_gt.json"
file2 = "output.json"
similarity_percentage = compare_json_files(file1, file2)
print("Accuracy of the model (% of correct predictions):\n", similarity_percentage)

Accuracy of the model (% of correct predictions):
 65.97853014037986


Output info